In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/mnist-dataset/dataset/format.json
/kaggle/input/mnist-dataset/dataset/test/class_6/img_687.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_421.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_837.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_834.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_782.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_264.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_408.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_367.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_456.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_677.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_144.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_40.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_606.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_829.png
/kaggle/input/mnist-dataset/dataset/test/class_6/img_242.png
/kaggle/input/mnist-dataset/dataset/te

In [2]:
import torch

print(torch.__version__)

2.5.1+cu124


In [3]:
!ls

__notebook__.ipynb


In [4]:
!pwd

/kaggle/working


In [5]:
!ls /kaggle/input

mnist-dataset


In [6]:
!ls /kaggle/input/mnist-dataset

dataset


In [7]:
import torch
import torch.nn as nn
import torch.optim as optim
import torch.utils.data as data
import torch.nn.functional as F

In [8]:
from tqdm import tqdm

In [9]:
import torchvision
import torchvision.transforms.v2 as tfs

In [10]:
import json
import os

In [11]:
from PIL import Image

In [12]:
os.listdir('/kaggle/input/mnist-dataset/dataset/test')

['class_6',
 'class_1',
 'class_2',
 'class_8',
 'class_5',
 'class_7',
 'class_9',
 'class_0',
 'class_4',
 'class_3']

In [13]:
class DigitDataset(data.Dataset):
    def __init__(self, path, train=True, transforms=None):
        self.path = os.path.join(path, 'train' if train else 'test')
        self.transforms = transforms

        with open(os.path.join(path, 'format.json'),'r') as f:
            self.format = json.load(f)
        self.length = 0
        self.files = []
        for class_name, target_name in self.format.items():
            file_dir = os.path.join(self.path, class_name)
            file_lists = os.listdir(file_dir)
            self.length += len(file_lists)
            for file_name in file_lists:
                img_path = os.path.join(file_dir, file_name)
                self.files.append((img_path, target_name))
        

    def __getitem__(self, item):
        file, target = self.files[item]
        img = Image.open(file) 
        if self.transforms:
            img = self.transforms(img)
        return img, target

    def __len__(self):
        return self.length

In [14]:
transforms = tfs.Compose([tfs.ToImage(),  tfs.ToDtype(torch.float32, scale=True), tfs.Lambda(lambda x:x.ravel())])
d_train = DigitDataset('/kaggle/input/mnist-dataset/dataset', train=True, transforms=transforms)

In [15]:
len(d_train)

60000

In [16]:
x,y = d_train[0]

In [17]:
x

tensor([0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 

In [18]:
y

0

In [19]:
type(x)

torch.Tensor

In [20]:
x.size()

torch.Size([784])

In [21]:
x, y = d_train[8000]

In [22]:
x

tensor([0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 

In [23]:
y

1

In [24]:
x.size()

torch.Size([784])

In [25]:
class DigitNN(nn.Module):
    def __init__(self, inp_dim, hid_dim1, hid_dim2, out_dim):
        super().__init__()
        self.layer1 = nn.Linear(inp_dim, hid_dim1)
        self.layer2 = nn.Linear(hid_dim1, hid_dim2)
        self.layer3 = nn.Linear(hid_dim2, out_dim)

    def forward(self, x):
        x = self.layer1(x)
        x = F.relu(x)
        x = self.layer2(x)
        x = F.relu(x)
        x = self.layer3(x)
        return x

In [26]:
transforms = tfs.Compose([tfs.ToImage(),  tfs.ToDtype(torch.float32, scale=True), tfs.Lambda(lambda x:x.ravel())])

d_train = DigitDataset('/kaggle/input/mnist-dataset/dataset', train=True, transforms=transforms)
d_test = DigitDataset('/kaggle/input/mnist-dataset/dataset', train=False, transforms=transforms)

train, val = data.random_split(d_train, [0.7, 0.3])
data_train = data.DataLoader(train, batch_size=32, shuffle=True)
data_val = data.DataLoader(val, batch_size=32, shuffle=False)

data_test = data.DataLoader(d_test, batch_size=500, shuffle=False)

model = DigitNN(784, 128, 64, 10)
epochs = 10
optimizer = optim.Adam(params = model.parameters(), lr = 0.01, weight_decay = 0.0001)
loss_func = nn.CrossEntropyLoss()

model.train()

train_losses = []
val_losses = []
for e in range(epochs):
    lm_count = 0
    loss_mean = 0
    tqdm_train = tqdm(data_train, leave=True)
    for x_train, y_train in tqdm_train:
        prediction = model(x_train)
        loss = loss_func(prediction, y_train)
        lm_count += 1
        loss_mean = 1/lm_count * loss.item() + (1 - 1/lm_count)*loss_mean
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        tqdm_train.set_description(f'{e+1}/{epochs} loss_mean = {loss_mean}')
        train_losses.append(loss_mean)

    tqdm_val = tqdm(data_val, leave = True)
    Q = 0
    for x_val, y_val in tqdm_val:
        pred = model(x_val)
        loss_val = loss_func(pred, y_val)
        Q += loss_val
    Q = Q / len(x_val)
    print(f'val_mean = {Q}')
    val_losses.append(Q)

st = model.state_dict()
torch.save(st, 'digit_model.pth')

100%|██████████| 563/563 [00:51<00:00, 10.85it/s]


val_mean = 7.960576057434082


100%|██████████| 563/563 [00:18<00:00, 30.86it/s]


val_mean = 7.367469787597656


100%|██████████| 563/563 [00:18<00:00, 30.07it/s]


...

val_mean = 6.458535194396973


100%|██████████| 563/563 [00:20<00:00, 27.96it/s]


val_mean = 6.01363468170166


100%|██████████| 563/563 [00:20<00:00, 27.79it/s]

val_mean = 6.0815606117248535


In [27]:
st = torch.load('digit_model.pth', weights_only=True)
model.load_state_dict(st)

model.eval()
for x_test, y_test in data_test:
    with torch.no_grad():
        pred_test = model(x_test)
        p = torch.argmax(pred_test, dim=1)
        acc = (p == y_test).float().mean().item()
        print(f"Accuracy = {acc}")

Accuracy = 0.9919999837875366
Accuracy = 0.9879999756813049
Accuracy = 0.984000027179718
Accuracy = 0.9900000095367432
Accuracy = 0.9539999961853027
Accuracy = 0.9559999704360962
Accuracy = 0.9319999814033508
Accuracy = 0.9240000247955322
Accuracy = 0.9679999947547913
Accuracy = 0.9860000014305115
Accuracy = 0.9340000152587891
Accuracy = 0.9179999828338623
Accuracy = 0.9639999866485596
Accuracy = 0.9639999866485596
Accuracy = 0.9459999799728394
Accuracy = 0.9620000123977661
Accuracy = 0.9559999704360962
Accuracy = 0.9380000233650208
Accuracy = 0.8880000114440918
Accuracy = 0.9340000152587891


# ONE-HOT-пен мысал

In [28]:
class DigitDataset(data.Dataset):
    def __init__(self, path, train=True, transforms=None):
        self.path = os.path.join(path, 'train' if train else 'test')
        self.transforms = transforms

        with open(os.path.join(path, 'format.json'),'r') as f:
            self.format = json.load(f)
        self.targets = torch.eye(10)
        self.length = 0
        self.files = []
        for class_name, target_name in self.format.items():
            file_dir = os.path.join(self.path, class_name)
            file_lists = os.listdir(file_dir)
            self.length += len(file_lists)
            for file_name in file_lists:
                img_path = os.path.join(file_dir, file_name)
                self.files.append((img_path, self.targets[target_name]))
        

    def __getitem__(self, item):
        file, target = self.files[item]
        img = Image.open(file) 
        if self.transforms:
            img = self.transforms(img)
        return img, target

    def __len__(self):
        return self.length

In [29]:
transforms = tfs.Compose([tfs.ToImage(),  tfs.ToDtype(torch.float32, scale=True), tfs.Lambda(lambda x:x.ravel())])
d_train = DigitDataset('/kaggle/input/mnist-dataset/dataset', train=True, transforms=transforms)

In [30]:
x, y = d_train[0]

In [31]:
x

tensor([0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000, 0.0000,
        0.0000, 0.0000, 0.0000, 0.0000, 

In [32]:
x.size()

torch.Size([784])

In [33]:
y

tensor([1., 0., 0., 0., 0., 0., 0., 0., 0., 0.])

In [34]:
len(d_train)

60000

In [35]:
x, y = d_train[30000]
y

tensor([0., 0., 0., 0., 1., 0., 0., 0., 0., 0.])

In [36]:
class DigitNN(nn.Module):
    def __init__(self, inp_dim, hid_dim1, hid_dim2, out_dim):
        super().__init__()
        self.layer1 = nn.Linear(inp_dim, hid_dim1)
        self.layer2 = nn.Linear(hid_dim1, hid_dim2)
        self.layer3 = nn.Linear(hid_dim2, out_dim)

    def forward(self, x):
        x = self.layer1(x)
        x = F.relu(x)
        x = self.layer2(x)
        x = F.relu(x)
        x = self.layer3(x)
        return x

In [37]:
transforms = tfs.Compose([tfs.ToImage(),  tfs.ToDtype(torch.float32, scale=True), tfs.Lambda(lambda x:x.ravel())])

d_train = DigitDataset('/kaggle/input/mnist-dataset/dataset', train=True, transforms=transforms)
d_test = DigitDataset('/kaggle/input/mnist-dataset/dataset', train=False, transforms=transforms)

train, val = data.random_split(d_train, [0.7, 0.3])
data_train = data.DataLoader(train, batch_size=32, shuffle=True)
data_val = data.DataLoader(val, batch_size=32, shuffle=False)

data_test = data.DataLoader(d_test, batch_size=500, shuffle=False)

model = DigitNN(784, 128, 64, 10)
epochs = 10
optimizer = optim.Adam(params = model.parameters(), lr = 0.01, weight_decay = 0.0001)
loss_func = nn.CrossEntropyLoss()

model.train()

train_losses = []
val_losses = []
for e in range(epochs):
    lm_count = 0
    loss_mean = 0
    tqdm_train = tqdm(data_train, leave=True)
    for x_train, y_train in tqdm_train:
        prediction = model(x_train)
        loss = loss_func(prediction, y_train)
        lm_count += 1
        loss_mean = 1/lm_count * loss.item() + (1 - 1/lm_count)*loss_mean
        
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()

        tqdm_train.set_description(f'{e+1}/{epochs} loss_mean = {loss_mean}')
        train_losses.append(loss_mean)

    tqdm_val = tqdm(data_val, leave = True)
    Q = 0
    for x_val, y_val in tqdm_val:
        pred = model(x_val)
        loss_val = loss_func(pred, y_val)
        Q += loss_val
    Q = Q / len(x_val)
    print(f'val_mean = {Q}')
    val_losses.append(Q)

st = model.state_dict()
torch.save(st, 'digit_model_one_hot.pth')

100%|██████████| 563/563 [00:19<00:00, 28.32it/s]


val_mean = 6.839493274688721


100%|██████████| 563/563 [00:19<00:00, 28.39it/s]


val_mean = 8.611711502075195


100%|██████████| 563/563 [00:19<00:00, 28.33it/s]


...

val_mean = 5.877331733703613


100%|██████████| 563/563 [00:19<00:00, 29.30it/s]


val_mean = 7.101245403289795


100%|██████████| 563/563 [00:19<00:00, 28.29it/s]

val_mean = 5.950746536254883


In [38]:
import torch

model = DigitNN(784, 128, 64, 10)


st = torch.load('digit_model_one_hot.pth', weights_only=True)
model.load_state_dict(st)

model.eval()
for x_test, y_test in data_test:
    with torch.no_grad():
        pred_test = model(x_test)
        p1 = torch.argmax(pred_test, dim=1)
        p2 = torch.argmax(y_test, dim=1)
        acc = (p1 == p2).float().mean().item()
        print(f"Accuracy = {acc}")

Accuracy = 0.9620000123977661
Accuracy = 0.9679999947547913
Accuracy = 0.9739999771118164
Accuracy = 0.9779999852180481
Accuracy = 0.9319999814033508
Accuracy = 0.9300000071525574
Accuracy = 0.9399999976158142
Accuracy = 0.9419999718666077
Accuracy = 0.9520000219345093
Accuracy = 0.9679999947547913
Accuracy = 0.9419999718666077
Accuracy = 0.9440000057220459
Accuracy = 0.9620000123977661
Accuracy = 0.9679999947547913
Accuracy = 0.9539999961853027
Accuracy = 0.9639999866485596
Accuracy = 0.9700000286102295
Accuracy = 0.9679999947547913
Accuracy = 0.9419999718666077
Accuracy = 0.9399999976158142
